# Machine Learning Engineer Nanodegree
## Deep Learning
## Project: Build a Digit Recognition Program

In this notebook, a template is provided for you to implement your functionality in stages which is required to successfully complete this project. If additional code is required that cannot be included in the notebook, be sure that the Python code is successfully imported and included in your submission, if necessary. Sections that begin with **'Implementation'** in the header indicate where you should begin your implementation for your project. Note that some sections of implementation are optional, and will be marked with **'Optional'** in the header.

In addition to implementing code, there will be questions that you must answer which relate to the project and your implementation. Each section where you will answer a question is preceded by a **'Question'** header. Carefully read each question and provide thorough answers in the following text boxes that begin with **'Answer:'**. Your project submission will be evaluated based on your answers to each of the questions and the implementation you provide.

>**Note:** Code and Markdown cells can be executed using the **Shift + Enter** keyboard shortcut. In addition, Markdown cells can be edited by typically double-clicking the cell to enter edit mode.

----
## Step 1: Design and Test a Model Architecture
Design and implement a deep learning model that learns to recognize sequences of digits. Train the model using synthetic data generated by concatenating character images from [notMNIST](http://yaroslavvb.blogspot.com/2011/09/notmnist-dataset.html) or [MNIST](http://yann.lecun.com/exdb/mnist/). To produce a synthetic sequence of digits for testing, you can for example limit yourself to sequences up to five digits, and use five classifiers on top of your deep network. You would have to incorporate an additional ‘blank’ character to account for shorter number sequences.

There are various aspects to consider when thinking about this problem:
- Your model can be derived from a deep neural net or a convolutional network.
- You could experiment sharing or not the weights between the softmax classifiers.
- You can also use a recurrent network in your deep neural net to replace the classification layers and directly emit the sequence of digits one-at-a-time.

You can use ** Keras ** to implement your model. Read more at [keras.io](https://keras.io/).

Here is an example of a [published baseline model on this problem](http://static.googleusercontent.com/media/research.google.com/en//pubs/archive/42241.pdf). ([video](https://www.youtube.com/watch?v=vGPI_JvLoN0)). You are not expected to model your architecture precisely using this model nor get the same performance levels, but this is more to show an exampe of an approach used to solve this particular problem. We encourage you to try out different architectures for yourself and see what works best for you. Here is a useful [forum post](https://discussions.udacity.com/t/goodfellow-et-al-2013-architecture/202363) discussing the architecture as described in the paper and here is [another one](https://discussions.udacity.com/t/what-loss-function-to-use-for-multi-digit-svhn-training/176897) discussing the loss function.

### Implementation
Use the code cell (or multiple code cells, if necessary) to implement the first step of your project. Once you have completed your implementation and are satisfied with the results, be sure to thoroughly answer the questions that follow.

In [1]:
# These are all the modules we'll be using later. Make sure you can import them
# before proceeding further.
from __future__ import print_function
import numpy as np
import tensorflow as tf
from six.moves import cPickle as pickle
from six.moves import range
import time
pickle_file = 'merge_notMNIST.pickle'
start = time.time()
with open(pickle_file, 'rb') as f:
  save = pickle.load(f)
  train_datasets = save['train_dataset']
  train_labels = save['train_labels'] #five classifier labels save as an string
  valid_datasets = save['valid_dataset']
  valid_labels = save['valid_labels']#five classifier labels save as an string
  test_datasets = save['test_dataset']
  test_labels = save['test_labels']#five classifier labels save as an string
  del save  # hint to help gc free up memory
  print('test set size', train_datasets.shape, train_labels.shape)
  print('valid set size', valid_datasets.shape, valid_labels.shape)
  print('Test set size', test_datasets.shape, test_labels.shape)
end = time.time()
print('reading data cost',round(end-start,6),'s')


test set size (70000, 28, 140) (70000,)
valid set size (10000, 28, 140) (10000,)
Test set size (10000, 28, 140) (10000,)
reading data cost 1.81393 s


In [3]:
from keras.models import Model,Sequential
from keras.layers import Dense,Dropout,Activation,Flatten,Input
from keras.layers.convolutional import Convolution2D ,MaxPooling2D 
from keras.optimizers import SGD
from keras.callbacks import EarlyStopping
from keras.utils.visualize_util import plot, model_to_dot
from IPython.display import Image, SVG
%matplotlib inline
%config InlineBackend.figure_format = 'retina'

In [4]:
image_size = 28
class_result = 11
class_model = 5
label_mat = ['A','B','C','D','E','F','G','H','I','J','N']
classify_num = len(label_mat)
def reformat(datasets,labels):
    label_len = labels.shape[0]
    
    dataset = datasets.reshape((label_len,image_size,5 * image_size,1)).astype(np.float32)
    
    labels_out = [np.ndarray((label_len,classify_num),dtype = np.float32) for i in range(class_model)]
    for i in range(5):
        for idx in range(label_len):
            labels_out[i][idx,:] = (np.array(labels[idx][i]) == label_mat).astype(np.float32)
    return dataset,labels_out
start = time.time()
train_dataset,train_label = reformat(train_datasets,train_labels)
valid_dataset,valid_label = reformat(valid_datasets,valid_labels)
test_dataset,test_label = reformat(test_datasets,test_labels)
end = time.time()
print('tranform data cost',round(end-start,6),'s')
#print('train set size', train_dataset.shape, len(train_label))
#print('valid set size', valid_dataset.shape, valid_label.shape)
#print('test set size', test_dataset.shape, test_label.shape)

tranform data cost 3.860998 s


In [ ]:
input_data = Input(shape=(image_size,5*image_size,1))
x = Convolution2D( 32,3,3, activation='relu')(input_data)
x = Convolution2D( 32,3,3, activation='relu')(x)
x = MaxPooling2D(pool_size=(2,2))(x)

x = Convolution2D( 64,3,3, activation='relu')(x)
x = Convolution2D( 64,3,3, activation='relu')(x)
x = MaxPooling2D(pool_size=(2,2))(x)

x = Convolution2D( 128,3,3, activation='relu')(x)
x = x = MaxPooling2D(pool_size=(2,2))(x)

x = Flatten()(x)

x = Dense(256, activation='relu')(x)
x = Dropout(0.5)(x)

result = [Dense(class_result, activation='softmax')(x) for i in range(5)]

model = Model(input=input_data, output=result)
early_stop = EarlyStopping(monitor='val_loss',patience=1)
model.compile(loss='categorical_crossentropy', optimizer='adadelta', metrics=['accuracy'])

#display model structure
plot(model, to_file='model.png',show_shapes=True)
Image('model.png')
#train your model
model.fit(train_dataset,
          train_label,
          batch_size=100,
          validation_data=(valid_dataset,valid_label),
          nb_epoch=50,
          shuffle=True,
          verbose=1,
          callbacks=[early_stop]
         )


Train on 70000 samples, validate on 10000 samples
Epoch 1/50
70000/70000 [==============================] - 1658s - loss: 9.2202 - dense_2_loss: 1.8684 - dense_3_loss: 1.8076 - dense_4_loss: 1.8114 - dense_5_loss: 1.8125 - dense_6_loss: 1.9203 - dense_2_acc: 0.3336 - dense_3_acc: 0.3556 - dense_4_acc: 0.3559 - dense_5_acc: 0.3550 - dense_6_acc: 0.3123 - val_loss: 3.1186 - val_dense_2_loss: 0.6430 - val_dense_3_loss: 0.5896 - val_dense_4_loss: 0.5888 - val_dense_5_loss: 0.6065 - val_dense_6_loss: 0.6905 - val_dense_2_acc: 0.8141 - val_dense_3_acc: 0.8313 - val_dense_4_acc: 0.8283 - val_dense_5_acc: 0.8236 - val_dense_6_acc: 0.8043

In [ ]:
def evaluate(model):
    right = 0
    error = 0
    for i in range(test_dataset.shape[0]):
        right_num = 0
        y_pred = model.predict(test_dataset[i].reshape(1,image_size,5*image_size,1))
        for j in range(class_model):
            if np.argmax(test_label[j][i]) == np.argmax(y_pred[j]):
                right_num = right_num + 1
        if right_num == class_model:
            right = right + 1
        else:
            error = error + 1
    return float(right)/(right+error)
evaluate(model)

In [22]:

'''
model = Sequential()
#first layer
model.add(Convolution2D( 6, 5, 5,border_mode='valid',input_shape=(image_size,5*image_size,1),activation='relu'))
model.add(MaxPooling2D(pool_size=(1,2)))
#model.add(Dropout(0.5))
#second layer
model.add(Convolution2D(12,5,5))
model.add(Activation('relu'))
model.add(MaxPooling2D(pool_size=(1,2)))
#model.add(Dropout(0.5))

model.add(Convolution2D(24,5,5))
model.add(Activation('relu'))
model.add(MaxPooling2D(pool_size=(1,2)))
#model.add(Dropout(0.5))#16 * 14,24ceng

model.add(Convolution2D(24,7,5))
model.add(Activation('relu'))
model.add(MaxPooling2D(pool_size=(2,2)))
#model.add(Dropout(0.5))#16 * 14,24ceng
#third layer
model.add(Flatten())
#fourth layer
model.add(Dense(120))
model.add(Activation('relu'))
model.add(Dropout(0.5))
#five layer
model.add(Dense(84))
model.add(Activation('relu'))
model.add(Dropout(0.5))
#output_layer(sixth)
model.add(Dense(classify_num,activation='softmax'))
model.compile(loss='categorical_crossentropy',optimizer='adam',metrics=['accuracy'])
return model
 
#build the model
for i in range(5):
    start = time.time()
    model = create_CNN_model()
    model.fit(train_dataset,
              train_label[:,0,i*classify_num:(i+1)*classify_num], 
              validation_data=(test_dataset,test_label[:,0,i*classify_num:(i+1)*classify_num]),
              nb_epoch=10,
              batch_size=64,
              verbose=1)                         
    scores = model.evaluate(test_dataset,test_label[:,0,i*classify_num:(i+1)*classify_num],verbose=1)
    print('cnn error:%.2f%%'%(100-scores[1]*100))
    end = time.time()
    print('model cost',round(end-start,6),'s')
'''



"\nmodel = Sequential()\n#first layer\nmodel.add(Convolution2D( 6, 5, 5,border_mode='valid',input_shape=(image_size,5*image_size,1),activation='relu'))\nmodel.add(MaxPooling2D(pool_size=(1,2)))\n#model.add(Dropout(0.5))\n#second layer\nmodel.add(Convolution2D(12,5,5))\nmodel.add(Activation('relu'))\nmodel.add(MaxPooling2D(pool_size=(1,2)))\n#model.add(Dropout(0.5))\n\nmodel.add(Convolution2D(24,5,5))\nmodel.add(Activation('relu'))\nmodel.add(MaxPooling2D(pool_size=(1,2)))\n#model.add(Dropout(0.5))#16 * 14,24ceng\n\nmodel.add(Convolution2D(24,7,5))\nmodel.add(Activation('relu'))\nmodel.add(MaxPooling2D(pool_size=(2,2)))\n#model.add(Dropout(0.5))#16 * 14,24ceng\n#third layer\nmodel.add(Flatten())\n#fourth layer\nmodel.add(Dense(120))\nmodel.add(Activation('relu'))\nmodel.add(Dropout(0.5))\n#five layer\nmodel.add(Dense(84))\nmodel.add(Activation('relu'))\nmodel.add(Dropout(0.5))\n#output_layer(sixth)\nmodel.add(Dense(classify_num,activation='softmax'))\nmodel.compile(loss='categorical_cro

### Question 1
_What approach did you take in coming up with a solution to this problem?_

**Answer:** 

### Question 2
_What does your final architecture look like? (Type of model, layers, sizes, connectivity, etc.)_

**Answer:**

### Question 3
_How did you train your model? How did you generate your synthetic dataset?_ Include examples of images from the synthetic data you constructed.

**Answer:**

----
## Step 2: Train a Model on a Realistic Dataset
Once you have settled on a good architecture, you can train your model on real data. In particular, the [Street View House Numbers (SVHN)](http://ufldl.stanford.edu/housenumbers/) dataset is a good large-scale dataset collected from house numbers in Google Street View. Training on this more challenging dataset, where the digits are not neatly lined-up and have various skews, fonts and colors, likely means you have to do some hyperparameter exploration to perform well.

### Implementation
Use the code cell (or multiple code cells, if necessary) to implement the first step of your project. Once you have completed your implementation and are satisfied with the results, be sure to thoroughly answer the questions that follow.

In [ ]:


### Your code implementation goes here.
### Feel free to use as many code cells as needed.



### Question 4
_Describe how you set up the training and testing data for your model. How does the model perform on a realistic dataset?_

**Answer:**

### Question 5
_What changes did you have to make, if any, to achieve "good" results? Were there any options you explored that made the results worse?_

**Answer:**

### Question 6
_What were your initial and final results with testing on a realistic dataset? Do you believe your model is doing a good enough job at classifying numbers correctly?_

**Answer:**

----
## Step 3: Test a Model on Newly-Captured Images

Take several pictures of numbers that you find around you (at least five), and run them through your classifier on your computer to produce example results. Alternatively (optionally), you can try using OpenCV / SimpleCV / Pygame to capture live images from a webcam and run those through your classifier.

### Implementation
Use the code cell (or multiple code cells, if necessary) to implement the first step of your project. Once you have completed your implementation and are satisfied with the results, be sure to thoroughly answer the questions that follow.

In [ ]:


### Your code implementation goes here.
### Feel free to use as many code cells as needed.



### Question 7
_Choose five candidate images of numbers you took from around you and provide them in the report. Are there any particular qualities of the image(s) that might make classification difficult?_

**Answer:**

### Question 8
_Is your model able to perform equally well on captured pictures or a live camera stream when compared to testing on the realistic dataset?_

**Answer:**

### Optional: Question 9
_If necessary, provide documentation for how an interface was built for your model to load and classify newly-acquired images._

**Answer:** Leave blank if you did not complete this part.

----
### Step 4: Explore an Improvement for a Model

There are many things you can do once you have the basic classifier in place. One example would be to also localize where the numbers are on the image. The SVHN dataset provides bounding boxes that you can tune to train a localizer. Train a regression loss to the coordinates of the bounding box, and then test it. 

### Implementation
Use the code cell (or multiple code cells, if necessary) to implement the first step of your project. Once you have completed your implementation and are satisfied with the results, be sure to thoroughly answer the questions that follow.

In [ ]:


### Your code implementation goes here.
### Feel free to use as many code cells as needed.



### Question 10
_How well does your model localize numbers on the testing set from the realistic dataset? Do your classification results change at all with localization included?_

**Answer:**

### Question 11
_Test the localization function on the images you captured in **Step 3**. Does the model accurately calculate a bounding box for the numbers in the images you found? If you did not use a graphical interface, you may need to investigate the bounding boxes by hand._ Provide an example of the localization created on a captured image.

**Answer:**

----
## Optional Step 5: Build an Application or Program for a Model
Take your project one step further. If you're interested, look to build an Android application or even a more robust Python program that can interface with input images and display the classified numbers and even the bounding boxes. You can for example try to build an augmented reality app by overlaying your answer on the image like the [Word Lens](https://en.wikipedia.org/wiki/Word_Lens) app does.

Loading a TensorFlow model into a camera app on Android is demonstrated in the [TensorFlow Android demo app](https://github.com/tensorflow/tensorflow/tree/master/tensorflow/examples/android), which you can simply modify.

If you decide to explore this optional route, be sure to document your interface and implementation, along with significant results you find. You can see the additional rubric items that you could be evaluated on by [following this link](https://review.udacity.com/#!/rubrics/413/view).

### Optional Implementation
Use the code cell (or multiple code cells, if necessary) to implement the first step of your project. Once you have completed your implementation and are satisfied with the results, be sure to thoroughly answer the questions that follow.

In [ ]:

    

### Your optional code implementation goes here.
### Feel free to use as many code cells as needed.



### Documentation
Provide additional documentation sufficient for detailing the implementation of the Android application or Python program for visualizing the classification of numbers in images. It should be clear how the program or application works. Demonstrations should be provided. 

_Write your documentation here._

> **Note**: Once you have completed all of the code implementations and successfully answered each question above, you may finalize your work by exporting the iPython Notebook as an HTML document. You can do this by using the menu above and navigating to  
**File -> Download as -> HTML (.html)**. Include the finished document along with this notebook as your submission.